In [13]:
from tune_sklearn import TuneSearchCV

from sklearn.ensemble import RandomForestClassifier
from sklearn.datasets import make_classification
from sklearn.metrics import f1_score

from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.model_selection import RepeatedKFold

from sklearn.model_selection import train_test_split

from sklearn import metrics
import pandas as pd
import numpy as np
%matplotlib inline
import matplotlib.pyplot as plt
from sklearn import tree
import xgboost as xgb

import multiprocessing

### Leemos los archivos

In [2]:
df_train_labels = pd.read_csv('./../datasets/train_labels.csv')
df_train_values = pd.read_csv('./../datasets/train_values_FE.csv')

#### Eliminamos el building id para pdoer hacer las predicciones

In [3]:
df_train_labels_filtrados = df_train_labels.drop(['building_id'], axis=1)
df_train_values_filtrados = df_train_values.drop(['building_id'], axis=1)

In [5]:
xg_reg = xgb.XGBClassifier()

In [20]:
# Grid de hiperparámetros evaluados
# ==============================================================================
param_grid = {
    'n_estimators'  : [100, 400],
#    'max_features'  : ['auto'],
    'max_depth'     : [6, 7],
    'subsample'     : [0.5],
    'learning_rate' : [0.01]
}

# Búsqueda por grid search con validación cruzada
# ==============================================================================
grid = GridSearchCV(
        estimator  = xg_reg,
        param_grid = param_grid,
        n_jobs     = multiprocessing.cpu_count() - 1,
        scoring    = 'neg_root_mean_squared_error',
        cv         = RepeatedKFold(n_splits=3, n_repeats=1, random_state=123), 
        refit      = True,
        verbose    = 0,
        return_train_score = True
       )

grid.fit(X = df_train_values_filtrados, y = df_train_labels_filtrados)

# Resultados
# ==============================================================================
resultados = pd.DataFrame(grid.cv_results_)
resultados

/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[18:21:55] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
0     746.041524      3.782262         0.800149        0.025244   
1    2976.658731     22.340540         2.906106        0.056287   
2     982.527837     15.185304         0.922064        0.020871   
3    3892.995267     20.096017         2.869084        0.686942   

  param_learning_rate param_max_depth param_n_estimators param_subsample  \
0                0.01               6                100             0.5   
1                0.01               6                400             0.5   
2                0.01               7                100             0.5   
3                0.01               7                400             0.5   

                                              params  split0_test_score  \
0  {'learning_rate': 0.01, 'max_depth': 6, 'n_est...          -0.580466   
1  {'learning_rate': 0.01, 'max_depth': 6, 'n_est...          -0.573793   
2  {'learning_rate': 0.01, 'max_depth': 7, 'n_est...          -0.576386   
3  {'learning_rate': 0.01, 'max_depth': 7, 'n_est...          -0.571411   

   split1_test_score  split2_test_score  mean_test_score  std_test_score  \
0          -0.581348          -0.581239        -0.581017        0.000393   
1          -0.571975          -0.575296        -0.573688        0.001358   
2          -0.576775          -0.577603        -0.576921        0.000507   
3          -0.569656          -0.572860        -0.571309        0.001310   

   rank_test_score  split0_train_score  split1_train_score  \
0                4           -0.579220           -0.580024   
1                2           -0.569752           -0.571018   
2                3           -0.574074           -0.574595   
3                1           -0.565472           -0.566454   

   split2_train_score  mean_train_score  std_train_score  
0           -0.579503         -0.579582         0.000333  
1           -0.570448         -0.570406         0.000518  
2           -0.573638         -0.574103         0.000391  
3           -0.566184         -0.566037         0.000414

In [23]:
res1 = resultados.filter(regex = '(param*|mean_t|std_t)') \
    .drop(columns = 'params') \
    .sort_values('mean_test_score', ascending = False)
res1

param_learning_rate param_max_depth param_n_estimators param_subsample  \
3                0.01               7                400             0.5   
1                0.01               6                400             0.5   
2                0.01               7                100             0.5   
0                0.01               6                100             0.5   

   mean_test_score  std_test_score  mean_train_score  std_train_score  
3        -0.571309        0.001310         -0.566037         0.000414  
1        -0.573688        0.001358         -0.570406         0.000518  
2        -0.576921        0.000507         -0.574103         0.000391  
0        -0.581017        0.000393         -0.579582         0.000333

In [ ]:
# Mejores hiperparámetros por validación cruzada
# ==============================================================================
print("----------------------------------------")
print("Mejores hiperparámetros encontrados (cv)")
print("----------------------------------------")
print(grid.best_params_, ":", grid.best_score_, grid.scoring)


In [ ]:
modelo_final = grid.best_estimator_

## SEGUNDA PRUEBA

### Primera iteración

In [61]:
%%time

from sklearn.experimental import enable_halving_search_cv
from sklearn.model_selection import HalvingGridSearchCV

param_grid = {
    "max_depth": [3, 7, 10],
    "gamma": [0, 0.5, 1],
    "reg_lambda": [0, 10],
    "scale_pos_weight": [1, 5],
    "subsample": [0.8],
    "colsample_bytree": [0.5],
    "n_estimators": [50, 100, 200]
}

xgb_cl = xgb.XGBClassifier(
    objective="multi:softprob", 
    verbose=False, 
    seed=42,
    learning_rate=0.02,
    nthread=3
)

halving_cv = HalvingGridSearchCV(
    xgb_cl, 
    param_grid, 
    scoring="f1_micro", 
    n_jobs=-1, 
    min_resources="smallest",
    factor=4
)

_ = halving_cv.fit(df_train_values_filtrados, df_train_labels_filtrados)

/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[21:17:26] WARNING: ../src/learner.cc:573: 
Parameters: { "scale_pos_weight", "verbose" } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[21:17:27] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
CPU times: user 2min 34s, sys: 236 ms, total: 2min 35s
Wall time: 13min 53s


In [62]:
halving_cv.best_params_

{'colsample_bytree': 0.5,
 'gamma': 0.5,
 'max_depth': 7,
 'n_estimators': 50,
 'reg_lambda': 10,
 'scale_pos_weight': 5,
 'subsample': 0.8}

In [63]:
halving_cv.best_score_

0.6576221170583115

### Segunda iteración

In [64]:
%%time

from sklearn.experimental import enable_halving_search_cv
from sklearn.model_selection import HalvingGridSearchCV

#    "scale_pos_weight": [1, 5, 10], es un dato a considerar mejorar en el futuro.
param_grid = {
    "max_depth": [3, 7, 8],
    "gamma": [0, 0.5, 1],
    "reg_lambda": [0, 5, 10],
    "subsample": [0.2, 0.5, 0.8],
    "colsample_bytree": [0, 0.5, 0.7],
    "n_estimators": [50, 200, 400],
    "learning_rate": [0.01, 0.1, 0.3, 0.5]
}

xgb_cl = xgb.XGBClassifier(
    objective="multi:softprob", 
    verbose=False, 
    seed=42,
    nthread=3
)

halving_cv = HalvingGridSearchCV(
    xgb_cl, 
    param_grid, 
    scoring="f1_micro", 
    n_jobs=-1, 
    min_resources="smallest",
    factor=4
)

_ = halving_cv.fit(df_train_values_filtrados, df_train_labels_filtrados)

/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[09:57:28] WARNING: ../src/learner.cc:573: 
Parameters: { "verbose" } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[09:57:30] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
CPU times: user 34min 59s, sys: 2.07 s, total: 35min 1s
Wall time: 12h 39min 51s


In [65]:
halving_cv.best_params_

{'colsample_bytree': 0.7,
 'gamma': 0,
 'learning_rate': 0.01,
 'max_depth': 8,
 'n_estimators': 400,
 'reg_lambda': 5,
 'subsample': 0.5}

In [66]:
halving_cv.best_score_

0.6780830367983206

In [5]:
%%time

from sklearn.experimental import enable_halving_search_cv
from sklearn.model_selection import HalvingGridSearchCV

#    "scale_pos_weight": [1, 5, 10], es un dato a considerar mejorar en el futuro.
param_grid = {
    "max_depth": [6, 8],
    "subsample": [0.5],
    "colsample_bytree": [0.7, 1],
    "n_estimators": [400, 600],
    "learning_rate": [0.01, 0.1]
}

xgb_cl = xgb.XGBClassifier(
    objective="multi:softprob", 
    verbose=False, 
    seed=42,
    nthread=3
)

halving_cv = HalvingGridSearchCV(
    xgb_cl, 
    param_grid, 
    scoring="f1_micro", 
    n_jobs=-1, 
    min_resources="smallest",
    factor=4
)

_ = halving_cv.fit(df_train_values_filtrados, df_train_labels_filtrados)

/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[19:33:49] WARNING: ../src/learner.cc:573: 
Parameters: { "verbose" } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[19:33:51] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
CPU times: user 33min 32s, sys: 590 ms, total: 33min 32s
Wall time: 19min 41s


In [6]:
halving_cv.best_params_

{'colsample_bytree': 0.7,
 'learning_rate': 0.1,
 'max_depth': 8,
 'n_estimators': 400,
 'subsample': 0.5}

In [7]:
halving_cv.best_score_

0.5355701754385965

KNN
gradient boosting trees
redes neuronales de sklearn
arbol de decisión

Cosas importantes para aprobar:
    - calidad de informe
    - calidad de video
    - tabla con todas las cosas que hemos probado para compensar el mal score

## Tercer intento

In [14]:
%%time

params = {
    "max_depth": [3, 7, 10],
    "subsample": [0.2, 0.5, 0.8],
    "colsample_bytree": [0, 0.5, 0.7],
    "n_estimators": [100, 300, 500, 800],
    "learning_rate": [0.01, 0.1, 0.3]
}

model = xgb.XGBClassifier(
    objective="multi:softprob",
    seed=42,
    nthread=3
)

xgb_cl = RandomizedSearchCV(
    model, 
    params, 
    scoring="f1_micro", 
    n_iter=20,
    verbose=1,
    random_state=42
)
X_train, X_test, y_train, y_test = train_test_split(df_train_values_filtrados, df_train_labels_filtrados, test_size=0.3, random_state=123)
eval_set = [(X_test, y_test)]
model_trained = xgb_cl.fit(X_train, y_train, early_stopping_rounds=10, verbose=True, eval_set=eval_set)

Fitting 5 folds for each of 20 candidates, totalling 100 fits


/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[12:38:10] WARNING: ../src/learner.cc:573: 
Parameters: { "n_iter_no_change", "tol", "validation_fraction", "verbose" } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[12:38:11] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[0]	validation_0-mlogloss:1.09473
[1]	validation_0-mlogloss:1.09059
[2]	validation_0-mlogloss:1.08643
[3]	validation_0-mlogloss:1.08218
[4]	validation_0-mlogloss:1.07828
[5]	validation_0-mlogloss:1.07464
[6]	validation_0-mlogloss:1.07078
[7]	validation_0-mlogloss:1.06711
[8]	validation_0-mlogloss:1.06324
[9]	validation_0-mlogloss:1.05955
[10]	validation_0-mlogloss:1

/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[12:39:23] WARNING: ../src/learner.cc:573: 
Parameters: { "n_iter_no_change", "tol", "validation_fraction", "verbose" } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[12:39:24] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[0]	validation_0-mlogloss:1.09467
[1]	validation_0-mlogloss:1.09059
[2]	validation_0-mlogloss:1.08640
[3]	validation_0-mlogloss:1.08217
[4]	validation_0-mlogloss:1.07827
[5]	validation_0-mlogloss:1.07461
[6]	validation_0-mlogloss:1.07073
[7]	validation_0-mlogloss:1.06706
[8]	validation_0-mlogloss:1.06323
[9]	validation_0-mlogloss:1.05954
[10]	validation_0-mlogloss:1

...

[16:01:17] WARNING: ../src/learner.cc:573: 
Parameters: { "n_iter_no_change", "tol", "validation_fraction", "verbose" } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[16:01:18] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[0]	validation_0-mlogloss:1.09631
[1]	validation_0-mlogloss:1.09360
[2]	validation_0-mlogloss:1.09103
[3]	validation_0-mlogloss:1.08851
[4]	validation_0-mlogloss:1.08604
[5]	validation_0-mlogloss:1.08385
[6]	validation_0-mlogloss:1.08152
[7]	validation_0-mlogloss:1.07909
[8]	validation_0-mlogloss:1.07692
[9]	validation_0-mlogloss:1.07463
[10]	validation_0-mlogloss:1

/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[16:01:38] WARNING: ../src/learner.cc:573: 
Parameters: { "n_iter_no_change", "tol", "validation_fraction", "verbose" } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[16:01:38] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[0]	validation_0-mlogloss:1.09631
[1]	validation_0-mlogloss:1.09360
[2]	validation_0-mlogloss:1.09104
[3]	validation_0-mlogloss:1.08851
[4]	validation_0-mlogloss:1.08604
[5]	validation_0-mlogloss:1.08381
[6]	validation_0-mlogloss:1.08126
[7]	validation_0-mlogloss:1.07910
[8]	validation_0-mlogloss:1.07692
[9]	validation_0-mlogloss:1.07464
[10]	validation_0-mlogloss:1

/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[16:01:58] WARNING: ../src/learner.cc:573: 
Parameters: { "n_iter_no_change", "tol", "validation_fraction", "verbose" } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[16:01:59] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[0]	validation_0-mlogloss:1.06086
[1]	validation_0-mlogloss:1.02410
[2]	validation_0-mlogloss:0.99542
[3]	validation_0-mlogloss:0.96659
[4]	validation_0-mlogloss:0.94006
[5]	validation_0-mlogloss:0.91926
[6]	validation_0-mlogloss:0.89627
[7]	validation_0-mlogloss:0.87546
[8]	validation_0-mlogloss:0.85898
[9]	validation_0-mlogloss:0.84377
[10]	validation_0-mlogloss:0

### Se hace la predicción

In [16]:
preds = model_trained.predict(X_test)

### Error de entrenamiento

In [19]:
xgb_cl.score(X_train, y_train)

0.7554325183642145

### Error de generalización o testing

In [20]:
xgb_cl.score(X_test, y_test)

0.7015003645386987

### Se calcula el error

In [21]:
score = f1_score(y_test, preds, average='micro')

In [22]:
print("El score es: " + str(score))

El score es: 0.7015003645386987


## Best params

In [23]:
xgb_cl.best_params_

{'verbose': 1,
 'validation_fraction': 0.2,
 'tol': 0.01,
 'subsample': 0.8,
 'n_iter_no_change': 5,
 'n_estimators': 800,
 'max_depth': 10,
 'learning_rate': 0.1,
 'colsample_bytree': 0.5}

## Cuarta iteración

In [30]:
%%time

params = {
    "max_depth": [7, 10, 12],
    "subsample": [0.5, 0.8, 1.0],
    "colsample_bytree": [0.3, 0.5, 0.6],
    "n_estimators": [500, 800, 1000],
    "learning_rate": [0.01, 0.1, 0.3],
    "num_parallel_tree": [2]
}

model = xgb.XGBClassifier(
    objective="multi:softprob",
    seed=42,
    nthread=3
)

xgb_cl = RandomizedSearchCV(
    model, 
    params, 
    scoring="f1_micro", 
    n_iter=22,
    verbose=1,
    random_state=42
)
X_train, X_test, y_train, y_test = train_test_split(df_train_values_filtrados, df_train_labels_filtrados, test_size=0.3, random_state=123)
eval_set = [(X_test, y_test)]
model_trained = xgb_cl.fit(X_train, y_train, early_stopping_rounds=10, verbose=True, eval_set=eval_set)

Fitting 5 folds for each of 22 candidates, totalling 110 fits


/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[16:33:55] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[0]	validation_0-mlogloss:1.09496
[1]	validation_0-mlogloss:1.09125
[2]	validation_0-mlogloss:1.08776
[3]	validation_0-mlogloss:1.08411
[4]	validation_0-mlogloss:1.08048
[5]	validation_0-mlogloss:1.07690
[6]	validation_0-mlogloss:1.07340
[7]	validation_0-mlogloss:1.06977
[8]	validation_0-mlogloss:1.06604
[9]	validation_0-mlogloss:1.06226
[10]	validation_0-mlogloss:1.05912
[11]	validation_0-mlogloss:1.05545
[12]	validation_0-mlogloss:1.05200
[13]	validation_0-mlogloss:1.04855
[14]	validation_0-mlogloss:1.04549
[15]	validation_0-mlogloss:1.04230
[16]	validation_0-mlogloss:1.03905
[17]	validation_0-mlogloss:1.03571
[18]	validation_0-mlogloss:1.03290
[19]	validation_0-mlogloss:1.02951
[20]	validation_0-mlogloss:1.02649
[21]	validation_0-mlog

/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[16:58:07] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[0]	validation_0-mlogloss:1.09496
[1]	validation_0-mlogloss:1.09125
[2]	validation_0-mlogloss:1.08773
[3]	validation_0-mlogloss:1.08410
[4]	validation_0-mlogloss:1.08048
[5]	validation_0-mlogloss:1.07690
[6]	validation_0-mlogloss:1.07340
[7]	validation_0-mlogloss:1.06976
[8]	validation_0-mlogloss:1.06603
[9]	validation_0-mlogloss:1.06225
[10]	validation_0-mlogloss:1.05911
[11]	validation_0-mlogloss:1.05543
[12]	validation_0-mlogloss:1.05198
[13]	validation_0-mlogloss:1.04853
[14]	validation_0-mlogloss:1.04548
[15]	validation_0-mlogloss:1.04229
[16]	validation_0-mlogloss:1.03904
[17]	validation_0-mlogloss:1.03571
[18]	validation_0-mlogloss:1.03289
[19]	validation_0-mlogloss:1.02951
[20]	validation_0-mlogloss:1.02650
[21]	validation_0-mlog

...

[08:02:29] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[0]	validation_0-mlogloss:1.09495
[1]	validation_0-mlogloss:1.09122
[2]	validation_0-mlogloss:1.08769
[3]	validation_0-mlogloss:1.08405
[4]	validation_0-mlogloss:1.08041
[5]	validation_0-mlogloss:1.07681
[6]	validation_0-mlogloss:1.07329
[7]	validation_0-mlogloss:1.06964
[8]	validation_0-mlogloss:1.06591
[9]	validation_0-mlogloss:1.06210
[10]	validation_0-mlogloss:1.05895
[11]	validation_0-mlogloss:1.05527
[12]	validation_0-mlogloss:1.05180
[13]	validation_0-mlogloss:1.04834
[14]	validation_0-mlogloss:1.04527
[15]	validation_0-mlogloss:1.04206
[16]	validation_0-mlogloss:1.03880
[17]	validation_0-mlogloss:1.03546
[18]	validation_0-mlogloss:1.03263
[19]	validation_0-mlogloss:1.02924
[20]	validation_0-mlogloss:1.02622
[21]	validation_0-mlog

/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[08:13:15] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[0]	validation_0-mlogloss:1.09496
[1]	validation_0-mlogloss:1.09123
[2]	validation_0-mlogloss:1.08770
[3]	validation_0-mlogloss:1.08406
[4]	validation_0-mlogloss:1.08042
[5]	validation_0-mlogloss:1.07683
[6]	validation_0-mlogloss:1.07331
[7]	validation_0-mlogloss:1.06966
[8]	validation_0-mlogloss:1.06593
[9]	validation_0-mlogloss:1.06213
[10]	validation_0-mlogloss:1.05899
[11]	validation_0-mlogloss:1.05531
[12]	validation_0-mlogloss:1.05185
[13]	validation_0-mlogloss:1.04839
[14]	validation_0-mlogloss:1.04531
[15]	validation_0-mlogloss:1.04211
[16]	validation_0-mlogloss:1.03885
[17]	validation_0-mlogloss:1.03551
[18]	validation_0-mlogloss:1.03268
[19]	validation_0-mlogloss:1.02930
[20]	validation_0-mlogloss:1.02627
[21]	validation_0-mlog

/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[08:23:57] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[0]	validation_0-mlogloss:1.05842
[1]	validation_0-mlogloss:1.02300
[2]	validation_0-mlogloss:0.99128
[3]	validation_0-mlogloss:0.95887
[4]	validation_0-mlogloss:0.93221
[5]	validation_0-mlogloss:0.91112
[6]	validation_0-mlogloss:0.88793
[7]	validation_0-mlogloss:0.86972
[8]	validation_0-mlogloss:0.85355
[9]	validation_0-mlogloss:0.83759
[10]	validation_0-mlogloss:0.82416
[11]	validation_0-mlogloss:0.81274
[12]	validation_0-mlogloss:0.80208
[13]	validation_0-mlogloss:0.79221
[14]	validation_0-mlogloss:0.78299
[15]	validation_0-mlogloss:0.77440
[16]	validation_0-mlogloss:0.76520
[17]	validation_0-mlogloss:0.75825
[18]	validation_0-mlogloss:0.75192
[19]	validation_0-mlogloss:0.74557
[20]	validation_0-mlogloss:0.74020
[21]	validation_0-mlog

### Se hace la predicción

In [31]:
preds = model_trained.predict(X_test)

### Error de entrenamiento

In [32]:
xgb_cl.score(X_train, y_train)

0.7671527244819647

### Error de generalización o testing

In [33]:
xgb_cl.score(X_test, y_test)

0.7023829319144037

### Se calcula el error

In [34]:
score = f1_score(y_test, preds, average='micro')

In [35]:
print("El score es: " + str(score))

El score es: 0.7023829319144037


## Best params

In [36]:
xgb_cl.best_params_

{'subsample': 0.8,
 'num_parallel_tree': 2,
 'n_estimators': 500,
 'max_depth': 12,
 'learning_rate': 0.1,
 'colsample_bytree': 0.5}

## Quinta iteracion

In [ ]:
params = {
    "max_depth": [7, 12],
    "subsample": [0.8],
    "colsample_bytree": [0.4, 0.5],
    "n_estimators": [500, 600],
    "learning_rate": [0.06, 0.1, 0.2],
    "min_child_weight": [1, 10],
    "sampling_method": ["uniform", "gradient_based"]
}

model_quinto = xgb.XGBClassifier(
    objective="multi:softprob",
    seed=42,
    nthread=3
)

xgb_cl_quinto = RandomizedSearchCV(
    model_quinto, 
    params, 
    scoring="f1_micro", 
    n_iter=10,
    verbose=1,
    random_state=42
)
X_train, X_test, y_train, y_test = train_test_split(df_train_values_filtrados, df_train_labels_filtrados, test_size=0.3, random_state=123)
eval_set = [(X_test, y_test)]
model_trained_quinto = xgb_cl_quinto.fit(X_train, y_train, early_stopping_rounds=10, verbose=True, eval_set=eval_set)

Fitting 5 folds for each of 16 candidates, totalling 80 fits


/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[12:10:33] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[0]	validation_0-mlogloss:1.07618
[1]	validation_0-mlogloss:1.05388
[2]	validation_0-mlogloss:1.03208
[3]	validation_0-mlogloss:1.01490
[4]	validation_0-mlogloss:0.99657
[5]	validation_0-mlogloss:0.98104
[6]	validation_0-mlogloss:0.96514
[7]	validation_0-mlogloss:0.95132
[8]	validation_0-mlogloss:0.93744
[9]	validation_0-mlogloss:0.92551
[10]	validation_0-mlogloss:0.91322
[11]	validation_0-mlogloss:0.90249
[12]	validation_0-mlogloss:0.89299
[13]	validation_0-mlogloss:0.88350
[14]	validation_0-mlogloss:0.87477
[15]	validation_0-mlogloss:0.86492
[16]	validation_0-mlogloss:0.85496
[17]	validation_0-mlogloss:0.84674
[18]	validation_0-mlogloss:0.83776
[19]	validation_0-mlogloss:0.83010
[20]	validation_0-mlogloss:0.82209
[21]	validation_0-mlog

/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[12:16:26] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[0]	validation_0-mlogloss:1.07618
[1]	validation_0-mlogloss:1.05391
[2]	validation_0-mlogloss:1.03207
[3]	validation_0-mlogloss:1.01493
[4]	validation_0-mlogloss:0.99657
[5]	validation_0-mlogloss:0.98098
[6]	validation_0-mlogloss:0.96507
[7]	validation_0-mlogloss:0.95129
[8]	validation_0-mlogloss:0.93737
[9]	validation_0-mlogloss:0.92541
[10]	validation_0-mlogloss:0.91309
[11]	validation_0-mlogloss:0.90242
[12]	validation_0-mlogloss:0.89293
[13]	validation_0-mlogloss:0.88347
[14]	validation_0-mlogloss:0.87474
[15]	validation_0-mlogloss:0.86491
[16]	validation_0-mlogloss:0.85507
[17]	validation_0-mlogloss:0.84685
[18]	validation_0-mlogloss:0.83784
[19]	validation_0-mlogloss:0.83020
[20]	validation_0-mlogloss:0.82221
[21]	validation_0-mlog

...

[15:38:19] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[0]	validation_0-mlogloss:1.03170
[1]	validation_0-mlogloss:0.97457
[2]	validation_0-mlogloss:0.92648
[3]	validation_0-mlogloss:0.89487
[4]	validation_0-mlogloss:0.86545
[5]	validation_0-mlogloss:0.84335
[6]	validation_0-mlogloss:0.82222
[7]	validation_0-mlogloss:0.80677
[8]	validation_0-mlogloss:0.79102
[9]	validation_0-mlogloss:0.77942
[10]	validation_0-mlogloss:0.76791
[11]	validation_0-mlogloss:0.75955
[12]	validation_0-mlogloss:0.75289
[13]	validation_0-mlogloss:0.74626
[14]	validation_0-mlogloss:0.74088
[15]	validation_0-mlogloss:0.73423
[16]	validation_0-mlogloss:0.72741
[17]	validation_0-mlogloss:0.72274
[18]	validation_0-mlogloss:0.71747
[19]	validation_0-mlogloss:0.71388
[20]	validation_0-mlogloss:0.71043
[21]	validation_0-mlog

/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[15:43:45] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[0]	validation_0-mlogloss:1.03178
[1]	validation_0-mlogloss:0.97441
[2]	validation_0-mlogloss:0.92640
[3]	validation_0-mlogloss:0.89488
[4]	validation_0-mlogloss:0.86559
[5]	validation_0-mlogloss:0.84348
[6]	validation_0-mlogloss:0.82232
[7]	validation_0-mlogloss:0.80687
[8]	validation_0-mlogloss:0.79115
[9]	validation_0-mlogloss:0.77942
[10]	validation_0-mlogloss:0.76813
[11]	validation_0-mlogloss:0.75979
[12]	validation_0-mlogloss:0.75305
[13]	validation_0-mlogloss:0.74645
[14]	validation_0-mlogloss:0.74101
[15]	validation_0-mlogloss:0.73438
[16]	validation_0-mlogloss:0.72772
[17]	validation_0-mlogloss:0.72304
[18]	validation_0-mlogloss:0.71779
[19]	validation_0-mlogloss:0.71429
[20]	validation_0-mlogloss:0.71086
[21]	validation_0-mlog

/home/nahuel/.local/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/nahuel/.local/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


[15:46:06] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softprob' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[0]	validation_0-mlogloss:1.03163
[1]	validation_0-mlogloss:0.97478
[2]	validation_0-mlogloss:0.92680
[3]	validation_0-mlogloss:0.89506
[4]	validation_0-mlogloss:0.86574
[5]	validation_0-mlogloss:0.84347
[6]	validation_0-mlogloss:0.82232
[7]	validation_0-mlogloss:0.80690
[8]	validation_0-mlogloss:0.79110
[9]	validation_0-mlogloss:0.77943
[10]	validation_0-mlogloss:0.76797
[11]	validation_0-mlogloss:0.75959
[12]	validation_0-mlogloss:0.75284
[13]	validation_0-mlogloss:0.74620
[14]	validation_0-mlogloss:0.74085
[15]	validation_0-mlogloss:0.73415
[16]	validation_0-mlogloss:0.72749
[17]	validation_0-mlogloss:0.72277
[18]	validation_0-mlogloss:0.71747
[19]	validation_0-mlogloss:0.71399
[20]	validation_0-mlogloss:0.71063
[21]	validation_0-mlog